# Analyzing results from humann3 run on time series MTX datasets previously analyzed in the paper: [Diel transcriptional response of a California Current plankton microbiome to light, low iron, and enduring viral infection](https://www.nature.com/articles/s41396-019-0472-2)

BioProject PRJNA492502: Searchable via: https://sra-explorer.info/  

**NOTE:** The following results were obtained by running HumanN3 with our custom DB: prok_euk_plankt_clustered_db_v2.1_201901b.dmnd  

Author: jayson.gutierrez@vliz.be

In [1]:
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib import cm
import seaborn as sns
import colorsys
from matplotlib.collections import PatchCollection


import Bio.SeqIO as bioseqio
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
#from Bio.Alphabet import IUPAC
from Bio import Entrez

from ete3 import NCBITaxa
from taxonomy_ranks import TaxonomyRanks


from subprocess import Popen, call, STDOUT, PIPE
import os
import shutil
import pandas as pd
import numpy as np
import matplotlib
import json
import glob
import re
import gzip
import sys
import csv
import time
import io
import pathlib
from collections import OrderedDict

from IPython.display import Image
from itertools import combinations
import itertools

In [2]:
#Customized functions for parsing and visualizing output data from HumanN-based profiling + our custo DB
from HumanN_data_processing import *

In [3]:
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px
###Uncomment below if necessary
rendef = "png" #"pdf" 
fig_renderer = pio.renderers[rendef]
fig_renderer.width = 1000
fig_renderer.height = 1000
pio.renderers.default = rendef

In [4]:
from sklearn.manifold import MDS
import sklearn.datasets as dt
from sklearn.metrics.pairwise import manhattan_distances, euclidean_distances
from scipy.spatial import distance

In [5]:
import warnings
warnings.filterwarnings("ignore")

In [6]:
matplotlib.rcParams['savefig.dpi'] = 900
matplotlib.rcParams['figure.dpi'] = 1000
sns.set_style("whitegrid", {'axes.grid' : False})
sns.set_context("paper")
sns.set(font='serif')
# sns.set_style("white", {
#         "font.family": "serif",
#         "font.serif": ["Times", "Palatino", "serif"]
#     })
sns.set_style('ticks')

In [7]:
###Utility functions

def format_tax_lbl(taxid = '94617', tax_lvl=[]):
    """Function to properly format taxonomic labels compatible with HumanN"""
    
    tax_lvls_lbls = ['superkingdom', 'phylum', 'class', 'order', 'family', 'genus', 'species']
    rank_taxon = TaxonomyRanks(taxid)
    rank_taxon.get_lineage_taxids_and_taxanames()
    rank_dict =  list(rank_taxon.lineages.values())[0]
    tax_tree = list(rank_taxon.lineages.values())[0]
    if(len(tax_lvl)==0):
        return tax_tree
    else:
        return [tax_tree[k][0] for k in tax_lvl]
    
def broad_tax_classif(pcl):
    '''Function to obtain a broader tax classification'''
    if 'Dinophyceae' in pcl:
        return 'Dinophyceae'
    elif 'Bacillariophyta' in pcl:
        return 'Bacillariophyta'
    elif 'Haptophyta' in pcl:
        return 'Haptophyta'
    elif 'Arthropoda' in pcl:
        return 'Arthropoda'
    elif 'Chlorophyta' in pcl:
        return 'Chlorophyta'
    elif 'Cyanobacteria' in pcl:
        return 'Cyanobacteria'
    elif 'Foraminifera' in pcl:
        return 'Foraminifera'
    elif 'Cryptophyceae' in pcl:
        return 'Cryptophyceae'
    elif 'Proteobacteria' in pcl:
        return 'Proteobacteria'
    elif 'Bacteroidetes' in pcl:
        return 'Bacteroidetes'
    elif 'Ciliophora' in pcl:
        return 'Ciliophora'
    elif 'Ascomycota' in pcl:
        return 'Ascomycota'
    else:
        return 'Other'

Loading cpm-normalized gene family abundances with human-readable metabolic rxns 

In [8]:
#Data output from humann run with default DBs (chocophlan + UniRef90 2020b)
cpm_norm_gene_rxn_renamed_df = pd.read_csv("data_PRJNA492502/joint_samples_regrouped2rxn-cpm-named.tsv", sep="\t")
cpm_norm_gene_rxn_renamed_df.head()

# Gene Family  \
0                                           UNMAPPED   
1                                          UNGROUPED   
2  UNGROUPED|g__Acanthamoeba.s__Acanthamoeba_lent...   
3  UNGROUPED|g__Acanthamoeba.s__Acanthamoeba_royr...   
4  UNGROUPED|g__Acaulopage.s__Acaulopage_tetracer...   

   SRR8039428_Abundance-CPM  SRR8039449_Abundance-CPM  \
0             814866.000000             757550.000000   
1             173289.366557             227953.244345   
2                 12.365865                  9.730667   
3                 21.173121                 14.414750   
4                  0.458659                  0.126449   

   SRR8039450_Abundance-CPM  SRR8039451_Abundance-CPM  \
0             758562.000000             793667.000000   
1             230194.042181             197593.783286   
2                  8.091712                 11.940651   
3                 10.957638                 15.636121   
4                  0.000000                  0.000000   

   SRR8039454_Abundance-CPM  SRR8039455_Abundance-CPM  \
0             823709.000000             826229.000000   
1             147422.605582             161781.311918   
2                  4.962327                  9.399106   
3                 12.938153                 13.420720   
4                  0.000000                  0.000000   

   SRR8039456_Abundance-CPM  SRR8039457_Abundance-CPM  \
0             810041.000000             635493.000000   
1             181603.001220             340679.429740   
2                  7.788238                  7.804292   
3                 14.214502                 14.960907   
4                  0.294080                  0.000000   

   SRR8039468_Abundance-CPM  SRR8039469_Abundance-CPM  \
0             825622.000000             493454.000000   
1             165961.332673             502986.511092   
2                  9.917122                  4.278331   
3                 14.889413                  5.502557   
4                  0.000000                  0.000000   

   SRR8039470_Abundance-CPM  SRR8039471_Abundance-CPM  \
0             816470.000000             835605.000000   
1             172172.220577             149751.045744   
2                 12.347064                 15.377136   
3                 16.774128                 19.028787   
4                  0.222523                  0.000000   

   SRR8039472_Abundance-CPM  SRR8039473_Abundance-CPM  
0             808100.000000             508181.000000  
1             165293.962872             486388.048170  
2                  9.041700                  7.945843  
3                 13.129387                  9.208495  
4                  0.000000                  0.000000

In [9]:
#Loading metadata file containing info on site and timing of sampling
metadata_df = pd.read_csv("data_PRJNA492502/sra_explorer_metadata.tsv", sep='\t')[['Accession','Title']]

In [10]:
cond_list0 = []
for gf in cpm_norm_gene_rxn_renamed_df['# Gene Family'].values:
    if ('UNMAPPED' in gf) or ('UNGROUPED' in gf):
        cond_list0.append(False)
    else:
        cond_list0.append(True)

#Finally, get a filtered df
index_list0 = cpm_norm_gene_rxn_renamed_df[cond_list0].sum(axis=1).sort_values(ascending=False).index.values
cpm_norm_gene_rxn_renamed_filtered_df = cpm_norm_gene_rxn_renamed_df.iloc[index_list0].reset_index(drop=True)
cpm_norm_gene_rxn_renamed_filtered_df.set_index(keys='# Gene Family', inplace=True)
#Here we further filter the df to keep only entrie linked to a given species
cpm_norm_gene_rxn_renamed_filtered_df2 = cpm_norm_gene_rxn_renamed_filtered_df.iloc[cpm_norm_gene_rxn_renamed_filtered_df.index.map(lambda s: '|g__' in s) ]

In [11]:
#Let's peek at top 5 most abundant rxns across all samples
cpm_norm_gene_rxn_renamed_filtered_df2.head()

SRR8039428_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  3878.510   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   541.626   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   438.850   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                   298.072   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   257.216   

                                                    SRR8039449_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  6401.050   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   609.160   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   573.527   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                   400.908   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   332.586   

                                                    SRR8039450_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  4984.790   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   339.402   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   349.213   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                   351.827   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   184.798   

                                                    SRR8039451_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                 2724.8100   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  325.6710   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  317.4110   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                  126.7997   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  166.8630   

                                                    SRR8039454_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                 17725.400   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  1209.570   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   834.759   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                   407.348   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                   545.302   

                                                    SRR8039455_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                 5593.4700   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  523.4100   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  496.7120   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                  192.3318   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  261.5270   

                                                    SRR8039456_Abundance-CPM  \
# Gene Family                                                                  
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                 2088.8200   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  478.0770   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  283.5600   
RIBULOSE-BISPHOSPHATE-CARBOXYLASE-RXN: (expasy)...                  245.7454   
PSII-RXN: (expasy) Photosystem II [1.10.3.9]|g_...                  208.8110   

                                                    SRR8039457_Abundance-CPM  \
# Gene Family                                

In [12]:
time_ordered_cols = ['09/16 6am', '09/16 10am', '09/16 2pm', '09/16 6pm', '09/16 10pm',
                     '09/17 2am', '09/17 6am', '09/17 10am', '09/17 2pm', '09/17 6pm', '09/17 10pm',
                     '09/18 2am', '09/18 6am']
#Rename original sample IDs to date and time of sampling
#Create mapper
sid2data = {}
for lsid in cpm_norm_gene_rxn_renamed_filtered_df2.columns:
    sid = lsid.split("_")[0]
    sid2data[lsid] = metadata_df[metadata_df['Accession']==sid].iloc[1][1].split(': ')[1]
    
cpm_norm_gene_rxn_renamed_filtered_df2.rename(sid2data, axis=1, inplace=True)

#Order columns by time
cpm_norm_gene_rxn_renamed_filtered_df2 = cpm_norm_gene_rxn_renamed_filtered_df2[time_ordered_cols]

In [13]:
#Simplify idx/col names 
day_dict = {"09/16":"D1","09/17":"D2","09/18":"D3"}

In [14]:
#Let's check which enzymes are the most active through time
tp_cont = []
pwy_name_cont = []
sps_name_cont = []
ec_abund_cont = []
for i in time_ordered_cols:
    top_ec = cpm_norm_gene_rxn_renamed_filtered_df2[i].sort_values(ascending=False).to_frame().iloc[0]
    tp = top_ec.index[0]
    tp_cont.append(tp)
    ec_abund = top_ec.values[0]
    ec_abund_cont.append(ec_abund)
    pwy_id,pwy_name,sps_name = top_ec.name.replace(": ","|").split("|")
    pwy_name_cont.append(pwy_name)
    sps_name_cont.append(sps_name)
#     print("On {}, Enzyme with E.C. {} from {}\nShowed abundance of: {}\n".format(tp,pwy_name,sps_name,ec_abund))

top_abund_enzyme = pd.DataFrame(data={"Enzyme_Abund":ec_abund_cont, "PWY_Name":pwy_name_cont, "Species":sps_name_cont},
                                index=tp_cont)

#Simplify idx names
top_abund_enzyme.index = top_abund_enzyme.index.map(lambda s: s.replace(s.split(" ")[0], day_dict[s.split(" ")[0]]).replace(' ',':'))

top_abund_enzyme

Enzyme_Abund                            PWY_Name  \
D1:6am        2088.82  (expasy) Photosystem II [1.10.3.9]   
D1:10am      11547.80  (expasy) Photosystem II [1.10.3.9]   
D1:2pm       17725.40  (expasy) Photosystem II [1.10.3.9]   
D1:6pm        5593.47  (expasy) Photosystem II [1.10.3.9]   
D1:10pm       3327.55  (expasy) Photosystem II [1.10.3.9]   
D2:2am        1141.64  (expasy) Photosystem II [1.10.3.9]   
D2:6am        6401.05  (expasy) Photosystem II [1.10.3.9]   
D2:10am       4984.79  (expasy) Photosystem II [1.10.3.9]   
D2:2pm       19022.70  (expasy) Photosystem II [1.10.3.9]   
D2:6pm        8369.38  (expasy) Photosystem II [1.10.3.9]   
D2:10pm       5045.08  (expasy) Photosystem II [1.10.3.9]   
D3:2am        2724.81  (expasy) Photosystem II [1.10.3.9]   
D3:6am        3878.51  (expasy) Photosystem II [1.10.3.9]   

                                                   Species  
D1:6am   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D1:10am  g__Chrysochromulina.s__Chrysochromulina_rotali...  
D1:2pm   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D1:6pm   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D1:10pm  g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:2am   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:6am   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:10am  g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:2pm   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:6pm   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D2:10pm  g__Chrysochromulina.s__Chrysochromulina_rotali...  
D3:2am   g__Chrysochromulina.s__Chrysochromulina_rotali...  
D3:6am   g__Chrysochromulina.s__Chrysochromulina_rotali...

The DF above shows that one species shows high abundance for a given enzyme, let's visualize this

In [15]:
# fig, ax = plt.subplots(figsize=(15,5))
# top_abund_enzyme.plot.bar(y='Enzyme_Abund', ax=ax, legend=False)
# ecn = top_abund_enzyme['PWY_Name'].value_counts().index[0].replace('(expasy) ','').replace('[','(EC ').replace(']',')')
# contrib_sps = top_abund_enzyme['Species'].value_counts().index[0]
# contrib_sps = contrib_sps.split("g__")[1].split("__")[1].replace('_',' ')
# ax.set_title("Abundance of {}\nContributing species: {}".format(ecn,contrib_sps), fontsize=15)
# ax.set_xlabel("Date-time")
# ax.set_ylabel("Counts per million mapped reads")
# sns.despine()
# fig.show()

#### Now, let's focus on analyzing metabolic pathway abundances across samples and the numerous taxa observed

In [16]:
table_fid = "data_PRJNA492502/joint_samples_path_abundance-cpm.tsv"
custom_db_pwy_abund_df = reshape_joint_pwy_abund_df(table_fid, "SRR")
custom_db_pwy_abund_df.to_csv("data_PRJNA492502/reshaped_joint_samples_path_abundance-cpm.tsv",sep="\t")
pwy_abund_full = pd.read_csv(table_fid,sep='\t')

In [17]:
#Grab all species-specific pawy abundances
idx2pwy_dict = pwy_abund_full['# Pathway'].to_dict()
idx_list = []
for k in idx2pwy_dict:
    v = idx2pwy_dict[k]
    if (v!='UNMAPPED') and ('UNINTEGRATED' not in v) and ('|g__' in v):
        idx_list.append(k)
        
#Filter out the original pwy abundance df
filtered_pwy_abund_full = pwy_abund_full.iloc[idx_list,:]
filtered_pwy_abund_full.reset_index(drop=True, inplace=True)

old_sample_ids = filtered_pwy_abund_full.iloc[:,1:].columns
new_sampled_ids = list(map(lambda s: s.split("_")[0],old_sample_ids))
#Rename column names
# filtered_pwy_abund_full.rename(columns=dict(zip(old_sample_ids,new_sampled_ids)),inplace=True)
filtered_pwy_abund_full.rename(columns=sid2data,inplace=True)

#Create intermediary DF to reshape filtered_pwy_abund_full
new_filtered_pwy_abund_full = pd.DataFrame.from_records(filtered_pwy_abund_full['# Pathway'].apply(lambda s: s.split('|')).values, 
                                                        columns=["PWY","Species"]).set_index("PWY")

#Reassign index and first column of filtered_pwy_abund_full
filtered_pwy_abund_full.index = new_filtered_pwy_abund_full.index
filtered_pwy_abund_full['# Pathway'] = new_filtered_pwy_abund_full['Species']
filtered_pwy_abund_full.rename(columns={'# Pathway':'Species'},inplace=True)

In [18]:
#Let's sort metabolic pathways based on their aggregated abundance observed across samples and species
agg_pwy_abund = filtered_pwy_abund_full.groupby("PWY").sum().sum(axis=1).sort_values(ascending=False)

In [19]:
#Sort and reorganize DF  
sorted_cols = list(itertools.chain(*[["Species"],time_ordered_cols]))
filtered_pwy_abund_full2 = filtered_pwy_abund_full.loc[agg_pwy_abund.index][sorted_cols]
#Rename columns in a more succint way
renamed_cols = top_abund_enzyme.index.values.tolist()
renamed_cols.insert(0,'Species')
filtered_pwy_abund_full2.columns = renamed_cols

In [20]:
#Add extra taxonomic classification to track down lower levels in the tree
ncbi_taxids_series = filtered_pwy_abund_full2["Species"].map(lambda s: s.split('__')[-1].replace('_', ' '))
tax_lvls = ['phylum','class']
extra_tax_lvls_series = ncbi_taxids_series.map(lambda s: format_tax_lbl(s, tax_lvls))
#Adding to main metabolic pathway DF a broad taxonomic group
filtered_pwy_abund_full2["TaxGroup"] = extra_tax_lvls_series.map(broad_tax_classif)

In [21]:
#Calcuate aggregated metabolic pathway abundance across major taxonomic groups
agg_metab_pwy_abund_df = filtered_pwy_abund_full2.groupby('TaxGroup').sum()
#Sorted by max metabolic pathway activity
agg_metab_pwy_abund_df = agg_metab_pwy_abund_df.loc[agg_metab_pwy_abund_df.sum(axis=1).sort_values(ascending=False).index]
#Log-transform data
#agg_metab_pwy_abund_df = agg_metab_pwy_abund_df.applymap(lambda x:np.log10(x+1))

The following stacked barchart gives an overview of how the prevalence of different major plankton groups in terms of aggregated metabolic activity changes at different time points on a daily basis 

In [ ]:
# color_list = sns.color_palette(None,n_colors=agg_metab_pwy_abund_df.index.shape[0])
fig, ax = plt.subplots(figsize=(20,13))
# tax_groups_col_list = plt.cm.get_cmap('jet_r', agg_metab_pwy_abund_df.shape[0])
# agg_metab_pwy_abund_df.T.plot.bar(stacked=True,ax=ax,colormap=tax_groups_col_list)
tax_groups_col_list = ['blue','blueviolet','aqua','#00C957',
                       'brown','greenyellow','red',
                       'black','pink','darkgreen','gold',
                       'grey','orange','green']

agg_metab_pwy_abund_df.T.plot(kind='bar', stacked=True, color=tax_groups_col_list, ax=ax)
ax.legend(title=None, ncol=4, fontsize=18, bbox_to_anchor=(0.22,0.81))
ax.set_xlabel("Sampling time point (day:time)", fontsize=30)
ax.set_ylabel("Aggregated metabolic pathway abundance\nCounts per million mapped reads (Log-scale)", fontsize=30)
ax.set_yscale('log')
ax.tick_params(axis='both',labelsize =24)
sns.despine()
fig.show()

Now let's reshape the DF above in a way that can be used for creating a clustermap with pathway specific abundances aggregated across major plankton taxonomic groups 

In [48]:
from matplotlib.pyplot import gcf

In [49]:
df_cont = []
pwy_id_list = agg_pwy_abund.index[:10]
for pwy_id in pwy_id_list:
    #Here we get the pathway-specific abundance aggregated across broad taxonomic groups
    subdf = filtered_pwy_abund_full2.iloc[:,1:].loc[pwy_id]
    if(len(subdf.shape)==1):
        new_subdf = subdf.to_frame().T.reset_index().rename(columns={'index': 'PWY'})
        new_subdf["PWY"] = new_subdf["PWY"][0].split(": ")[-1].capitalize()
        df_cont.append(new_subdf.set_index(['PWY','TaxGroup']))
        #df_cont.append(subdf.to_frame().T.reset_index().rename(columns={'index': 'PWY'}).set_index(['PWY','TaxGroup']))
    else:
        pwy_specific_abund_profiles = subdf.groupby('TaxGroup').sum()
        pwy_specific_abund_profiles["PWY"] = pwy_id.split(": ")[-1].capitalize()
        df_cont.append(pwy_specific_abund_profiles.reset_index().set_index(['PWY','TaxGroup']))
        
#Finally, stack up dfs and create one single df with multi-index: pwy and taxonomic groups. Data is log-transformed
pwy_tax_indexed_df = pd.concat(df_cont).applymap(lambda x: np.log10(1+x))

In [50]:
#Create a list of colors for the pwy ids on the y axis
##pwy_col_list = sns.cubehelix_palette(pwy_id_list.size, light=.9, dark=.1, reverse=True, start=1, rot=-2)
pwy_col_list = sns.color_palette(palette='Paired', n_colors=pwy_id_list.size)
pwy_id_col_map = dict(zip(pwy_id_list.map(lambda s: s.split(": ")[-1].capitalize()), pwy_col_list))
pwy_id_colors = [pwy_id_col_map[k] for k in pwy_tax_indexed_df.index.get_level_values('PWY')]
#Generating colors for taxa
tax_id_col_map = dict(zip(agg_metab_pwy_abund_df.index,tax_groups_col_list))
tax_id_colors = pwy_tax_indexed_df.index.get_level_values('TaxGroup').map(tax_id_col_map)

In [51]:
#Here we create a multi-index DF to propely assign colors to rows in the clustermap
get_pwy_cont = []
get_tax_cont = []
pwy_id_col_cont = []
tax_id_col_cont = []
for idx in pwy_tax_indexed_df.index:
    get_pwy, get_tax = idx
    get_pwy_cont.append(get_pwy)
    get_tax_cont.append(get_tax)
    pwy_id_col_cont.append(pwy_id_col_map[get_pwy])
    tax_id_col_cont.append(tax_id_col_map[get_tax])
    
arrays = [get_pwy_cont, get_tax_cont]
pwy_taxa_color_df = pd.DataFrame(data=zip(pwy_id_col_cont,tax_id_col_cont), columns=['PWY', 'TaxGroup'],
                                 index=pd.MultiIndex.from_arrays(arrays, names=('PWY', 'TaxGroup')))
# pwy_tax_indexed_df.index.names = [' ', ' ']

The following clustermap summarizes contributions by different taxonomic groups to metabolic pathway activities at different time points through the day, over 3 consecutive days. 

In [52]:
g = sns.clustermap(pwy_tax_indexed_df,
                   # Turn off the clustering
                   row_cluster=False, 
                   col_cluster=False,
                   metric=distance.braycurtis,
                   method="single",
                   # Add colored class labels using data frame created from node and network colors
                   row_colors = pwy_taxa_color_df,
                   col_colors = None,
                   # Make the plot look better when many rows/cols
                   linewidths=0.2,
                   xticklabels=True, 
                   yticklabels=False,
                   center=0, 
                   cmap="YlOrRd",
                   figsize=(10, 10), 
                   dendrogram_ratio=(0.2, 0.2),
                   cbar_kws = {
                               "label":"Counts per million mapped reads (Log-scale)",
                               "orientation":"vertical",
                               "shrink":0.1,
                               #"extend":"both", 
                               #"drawedges":True, 
                               #"extendfrac":0.01,
                               "ticks":np.arange(0,4)
                              }
                   )

g.ax_heatmap.set_ylabel(" ")

for label in pwy_id_col_map.keys():
    g.ax_col_dendrogram.bar(0, 0, color=pwy_id_col_map[label], label=label, 
                            linewidth=0, width=0.4)

l1 = g.ax_col_dendrogram.legend(title='PWY', loc="center", ncol=1, bbox_to_anchor=(0.025, 0.712), 
                                fontsize=8, bbox_transform=gcf().transFigure)


for label in tax_id_col_map.keys():
    g.ax_row_dendrogram.bar(0, 0, color=tax_id_col_map[label], label=label, 
                            linewidth=0, width=0.4)

l2 = g.ax_row_dendrogram.legend(title='TaxGroup', loc="center", ncol=2, bbox_to_anchor=(0.025, 0.53), 
                                fontsize=8, bbox_transform=gcf().transFigure)

g.cax.set_position([.965, .2, .03, .55])
#g.ax_heatmap.set_title("California Current plankton microbiome\n(BioProject accession number PRJNA492502)", fontsize=18)

plt.show()

#### Calculate dist matrix (BC) and run MDS to visualize data points in high dimensional space (vectors of metabolic pathway abundance per species) as 2D projections

In [53]:
#Compute distance matrix
X = filtered_pwy_abund_full2.iloc[:,1:-1].T.values
dist_matrix = np.zeros((X.shape[0],X.shape[0]))
for i in np.arange(X.shape[0]):
    for j in np.arange(X.shape[0]):
        dist_matrix[i,j] = distance.braycurtis(X[i],X[j])
        
#Run MDS
mds = MDS(dissimilarity='precomputed', random_state=0)
# Get the embeddings
X_transform = mds.fit_transform(dist_matrix)

In [54]:
#Redefine lbls here
lbls = top_abund_enzyme.index
#Create a list of colors to uniquely identify each time point
#unique_tps = pd.Series([s.split(':')[-1] for s in lbls]).unique()
ucs_dict = dict(zip(lbls,sns.color_palette(None,n_colors=lbls.shape[0])))
color_list = []
for lbl in lbls:
    color_list.append(ucs_dict[lbl])

Visualize 2D projections of data points

In [58]:
fig, ax = plt.subplots(figsize=(15,10))

y = X_transform[:,0]
z = X_transform[:,1]

u = np.diff(y)
v = np.diff(z)
pos_y = y[:-1] + u/2
pos_z = z[:-1] + v/2
norm = np.sqrt(u**2+v**2) 

ax.plot(y,z, marker=" ", alpha=0.25)

widths = np.repeat(0.5,pos_y.size)
ax.quiver(pos_y, pos_z, u/norm, v/norm, angles="xy", zorder=2, pivot="mid", scale=16.5, linewidths=widths, edgecolors='k')

ax.scatter(y, z, c=color_list, s=300, alpha=1)

for i, txt in enumerate(lbls):
    ax.annotate(txt, (y[i]-0.035, z[i]+0.035), fontsize=14)
ax.set_xlim([-.7,.7])
ax.set_ylim([-.6,.8])
# ax.set_xticks([])
# ax.set_yticks([])
# ax.set_title('Bray-Curtis distance')

ax.set_xlabel("MDS-1", fontsize=24)
ax.set_ylabel("MDS-2", fontsize=24)
ax.tick_params(axis='both',labelsize=20)

sns.despine()
fig.show()